In [1]:
import glob, re, os, sys
from gensim.models import Word2Vec
from gensim.models.callbacks import CallbackAny2Vec

In [2]:
import gensim
gensim.__version__

'4.0.1'

In [3]:
class MyCallback(CallbackAny2Vec):
    '''
    This callback performs the evaluation of the word embeddings through a series of tests.
    The tests are described in the paper https://arxiv.org/abs/1507.05523
    The tests implemented are "ws", "tfl", and "sem&syn"
    '''
    
    def __init__(self, embedding_name):
        self.epoch = 0
        self.embedding_name = embedding_name
        pass

    
    def on_epoch_end(self, model):
        
        if self.epoch%5==0:
            print("Epoch #{} end".format(self.epoch))
        
        # eval every 2 epochs
        if self.epoch%2==0:
            #training_loss = model.get_latest_training_loss()
            #print('Training loss: ', training_loss)

            # save the embeddings
            model.wv.save_word2vec_format('word_vectors.txt', write_header=False)
            
            interpreter = sys.executable

            # run the evaluations
            cmd = f'{interpreter} ../src/run_evaluation_embeddings.py \
            --emb_dim {model.vector_size} \
            --eval_files_path ../data/evaluation_tests_word_embedding/ \
            --embedding_file word_vectors.txt \
            --embedding_name {self.embedding_name+f"_epoch-{self.epoch}"} \
            --results_dir ../results/Word_embedding_quality_W2V/ \
            --log_file ../logs/Word_embedding_quality_W2V/log_{self.embedding_name+f"_epoch-{self.epoch}"}.log \
            --upper_and_lower True'
            os.system(cmd)


            # delete word embedding file
            os.remove('word_vectors.txt')
            
        self.epoch += 1

In [4]:
dim = 300
windows = [3, 5, 7]
n_epochss = [20, 40]

# keep all corpus files
corpus_files = glob.glob('../data/corpora*/*')
print("Corpus files: ", corpus_files)
print()

for corpus_file in corpus_files:
    
    corpus_name = corpus_file.split("/")[-1].rstrip(".cor")
    corpus_type = corpus_file.split("/")[-2]

    for w in windows:
        for n_epochs in n_epochss:

            if corpus_type=='corpora_lemmatized':
                embedding_name = f'W2V_lemmatized_dim-{dim}_w-{w}_alpha-default_epochs-{n_epochs}_corpus-{corpus_name}' 
            else:
                embedding_name = f'W2V_dim-{dim}_w-{w}_alpha-default_epochs-{n_epochs}_corpus-{corpus_name}' 

            print("Start training corpus: ", corpus_name)
            print("Embedding name: ", embedding_name)
                
            callback = MyCallback(embedding_name=embedding_name)
            model = Word2Vec(vector_size=dim, 
                             window=w, 
                             sg=1,
                             hs=0,
                             negative=5,  # default
                             ns_exponent=0.75, # default
                             #alpha=0.1, # Use only if making multiple calls to train(), when you want to manage the alpha learning-rate yourself (not recommended).
                             #min_alpha=0.0001, # default, linear decay of lr
                             min_count=5,
                             max_vocab_size=100000, 
                             workers=3,
                             )


            model.build_vocab(corpus_file=corpus_file)
            print('Vocab done...')
            print('Corpus count: ', model.corpus_count)
            print('Corpus total words: ', model.corpus_total_words)

            model.train(corpus_file=corpus_file,  
                        callbacks=[callback], 
                        total_examples=model.corpus_count,
                        total_words=model.corpus_total_words,
                        epochs=n_epochs
                        )


            print(f'End training of {embedding_name}')
            print()



Corpus files:  ['../data/corpora_lemmatized/female_person_artist_lyrics.cor', '../data/corpora_lemmatized/male_person_artist_lyrics.cor', '../data/corpora_lemmatized/all_person_artist_lyrics.cor', '../data/corpora/female_person_artist_lyrics.cor', '../data/corpora/male_person_artist_lyrics.cor', '../data/corpora/all_person_artist_lyrics.cor']

Start training corpus:  female_person_artist_lyrics
Embedding name:  W2V_lemmatized_dim-300_w-3_alpha-default_epochs-20_corpus-female_person_artist_lyrics
Vocab done...
Corpus count:  70880
Corpus total words:  15949187
Epoch #0 end


[2021-11-21 23:12:17,948 INFO] Start computation quality word embedding tests. Results will be saved at ../results/Word_embedding_quality_W2V/
[2021-11-21 23:12:17,951 INFO] Number of unique words for tests: 2066
[2021-11-21 23:12:17,951 INFO] Reading word vectors...
[2021-11-21 23:12:18,332 INFO] Number of word vectors read: 10000...
[2021-11-21 23:12:18,705 INFO] Number of word vectors read: 20000...
[2021-11-21 23:12:18,813 INFO] Number of word vectors found: 1099
[2021-11-21 23:12:18,814 INFO] Running: sed -i '' '1s/^/1099 300\'$'\n/' ../data/evaluation_tests_word_embedding/temp_embs.txt
[2021-11-21 23:12:18,844 INFO] Running WS test...
[2021-11-21 23:12:18,845 INFO] Calling command: ./../data/evaluation_tests_word_embedding/ws/ws ../data/evaluation_tests_word_embedding/temp_embs.txt > ../results/Word_embedding_quality_W2V/W2V_lemmatized_dim-300_w-3_alpha-default_epochs-20_corpus-female_person_artist_lyrics_epoch-0/ws_test.txt
[2021-11-21 23:12:18,948 INFO] Running TOEFL test...
[2

[2021-11-21 23:12:50,851 INFO] Test done!
[2021-11-21 23:12:50,851 INFO] -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*
[2021-11-21 23:13:50,454 INFO] Start computation quality word embedding tests. Results will be saved at ../results/Word_embedding_quality_W2V/
[2021-11-21 23:13:50,458 INFO] Number of unique words for tests: 2066
[2021-11-21 23:13:50,458 INFO] Reading word vectors...
[2021-11-21 23:13:50,883 INFO] Number of word vectors read: 10000...
[2021-11-21 23:13:51,260 INFO] Number of word vectors read: 20000...
[2021-11-21 23:13:51,373 INFO] Number of word vectors found: 1099
[2021-11-21 23:13:51,374 INFO] Running: sed -i '' '1s/^/1099 300\'$'\n/' ../data/evaluation_tests_word_embedding/temp_embs.txt
[2021-11-21 23:13:51,400 INFO] Running WS test...
[2021-11-21 23:13:51,401 INFO] Calling command: ./../data/evaluation_tests_word_embedding/ws/ws ../data/evaluation_tests_word_embedding/temp_embs.txt > ../results/Word_embedding_quality_W2V/W2V_lemmatized_dim-300_w-3_

[2021-11-21 23:14:21,410 INFO] Test done!
[2021-11-21 23:14:21,410 INFO] -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*
[2021-11-21 23:15:18,843 INFO] Start computation quality word embedding tests. Results will be saved at ../results/Word_embedding_quality_W2V/
[2021-11-21 23:15:18,846 INFO] Number of unique words for tests: 2066
[2021-11-21 23:15:18,846 INFO] Reading word vectors...
[2021-11-21 23:15:19,245 INFO] Number of word vectors read: 10000...
[2021-11-21 23:15:19,715 INFO] Number of word vectors read: 20000...
[2021-11-21 23:15:19,828 INFO] Number of word vectors found: 1099
[2021-11-21 23:15:19,828 INFO] Running: sed -i '' '1s/^/1099 300\'$'\n/' ../data/evaluation_tests_word_embedding/temp_embs.txt
[2021-11-21 23:15:19,852 INFO] Running WS test...
[2021-11-21 23:15:19,853 INFO] Calling command: ./../data/evaluation_tests_word_embedding/ws/ws ../data/evaluation_tests_word_embedding/temp_embs.txt > ../results/Word_embedding_quality_W2V/W2V_lemmatized_dim-300_w-3_

[2021-11-21 23:15:56,050 INFO] Test done!
[2021-11-21 23:15:56,050 INFO] -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*


...

Epoch #35 end


[2021-11-23 21:41:55,423 INFO] Start computation quality word embedding tests. Results will be saved at ../results/Word_embedding_quality_W2V/
[2021-11-23 21:41:55,427 INFO] Number of unique words for tests: 2066
[2021-11-23 21:41:55,428 INFO] Reading word vectors...
[2021-11-23 21:41:55,871 INFO] Number of word vectors read: 10000...
[2021-11-23 21:41:56,321 INFO] Number of word vectors read: 20000...
[2021-11-23 21:41:56,701 INFO] Number of word vectors read: 30000...
[2021-11-23 21:41:57,086 INFO] Number of word vectors read: 40000...
[2021-11-23 21:41:57,460 INFO] Number of word vectors read: 50000...
[2021-11-23 21:41:57,549 INFO] Number of word vectors found: 1423
[2021-11-23 21:41:57,549 INFO] Running: sed -i '' '1s/^/1423 300\'$'\n/' ../data/evaluation_tests_word_embedding/temp_embs.txt
[2021-11-23 21:41:57,582 INFO] Running WS test...
[2021-11-23 21:41:57,590 INFO] Calling command: ./../data/evaluation_tests_word_embedding/ws/ws ../data/evaluation_tests_word_embedding/temp_emb

[2021-11-23 21:42:51,803 INFO] Test done!
[2021-11-23 21:42:51,803 INFO] -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*
[2021-11-23 21:51:00,277 INFO] Start computation quality word embedding tests. Results will be saved at ../results/Word_embedding_quality_W2V/
[2021-11-23 21:51:00,286 INFO] Number of unique words for tests: 2066
[2021-11-23 21:51:00,286 INFO] Reading word vectors...
[2021-11-23 21:51:00,709 INFO] Number of word vectors read: 10000...
[2021-11-23 21:51:01,092 INFO] Number of word vectors read: 20000...
[2021-11-23 21:51:01,482 INFO] Number of word vectors read: 30000...
[2021-11-23 21:51:01,862 INFO] Number of word vectors read: 40000...
[2021-11-23 21:51:02,241 INFO] Number of word vectors read: 50000...
[2021-11-23 21:51:02,329 INFO] Number of word vectors found: 1423
[2021-11-23 21:51:02,329 INFO] Running: sed -i '' '1s/^/1423 300\'$'\n/' ../data/evaluation_tests_word_embedding/temp_embs.txt
[2021-11-23 21:51:02,384 INFO] Running WS test...
[2021-11-2

[2021-11-23 21:51:55,284 INFO] Test done!
[2021-11-23 21:51:55,284 INFO] -*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*-*


End training of W2V_dim-300_w-7_alpha-default_epochs-40_corpus-all_person_artist_lyrics

